# Autometa Data Descriptions and Formats

The Autometa pipeline will generate a number of files required for binning metagenomes into MAGs. These files correspond to different statistics and annotations respective to 

| File Name | File Description | File Format |
|------|------|------|
| \*filtered_ge_{length_cutoff}.fna | contigs greater than or equal to the provided `--length-cutoff` parameter | fasta |
| k-mers.tsv | contig x k-mer frequencies | wide |
| k-mers.normalized.tsv | contig x CLR normalized k-mer frequencies | wide |
| \*orfs.faa | prodigal-annotated amino-acid ORFs | fasta |
| \*orfs.fna | prodigal-annotated nucleotide ORFs | fasta |
| \*blastp.tsv | Diamond blastp search results table (outfmt 6) | long |
| \*blastp.pkl.gz | Autometa DiamondResult object used for taxonomic assignment | python pickled dict object |
| majority_vote.tsv | Autometa voted taxids | long |
| \*lca.tsv | ORF x LCA taxid | long |
| tour.pkl.gz | Autometa list object used for LCA assignment | python pickled list object |
| level.pkl.gz | Autometa list object used for LCA assignment | python pickled list object |
| occurrence.pkl.gz | Autometa list object used for LCA assignment | python pickled list object |
| sparse.pkl.gz | Autometa list object used for LCA assignment | python pickled numpy sparse table |
| \*.hmmscan.tsv | kingdom-specific hmmscan raw results table | long |
| \*.markers.tsv | kingdom-specific marker annotation table | long |

## Data handling methods

In [1]:
!cd ../
!echo "To setup and IDE using autometa's modules, navigate to the autometa base directory..."
!echo "I.e. Base directory : $(pwd)"

To setup and IDE using autometa's modules, navigate to the autometa base directory...
I.e. Base directory : /Users/rees/Wisc/kwan/tools/autometa/docs


In [2]:
import os
os.chdir('../')

In [3]:
# Import autometa utility function to load python pickled objects
from autometa.common.utilities import unpickle

# Import DiamondResult to allow unpickling blastp.pkl.gz results
from autometa.common.external.diamond import DiamondResult

## orfs.blastp.pkl.gz (dict of ORFs DiamondResult)

In [4]:
results = unpickle('dev/scaffolds.orfs.faa.blastp.pkl.gz')

Notice a utility function is provided to easily load the python serialized objects

The `DiamondResult` Autometa object holds a number of attributes as well as some methods that provide easy access to blastp results corresponding to any searched query seqid (ORF)

In [5]:
NODE_98_orf_5 = results.get('NODE_98_length_143507_cov_224.136_5')

# NODE_98_orf_5?

As you can see the `DiamondResult` object holds a number of attributes:

Attributes:
* qseqid
* pident
* length
* gapopen
* mismatch
* qstart
* qend
* sstart
* send
* length
* bitscore
* evalue
* sseqid
* sseqids

Methods:
* get_top_hit

Perhaps the most convenient attribute to query a `qseqid` of the ORF's `DiamondResult` object is `sseqids`.

i.e.

In [6]:
for sseqid, attrs in results.get('NODE_98_length_143507_cov_224.136_11').sseqids.items():
    print(
        f"sseqid: {sseqid} bitscore: {attrs.get('bitscore')} "
        f"taxid: {attrs.get('taxid')} "
    )

sseqid: WP_011577313.1 bitscore: 550.1 taxid: 212 
sseqid: WP_021308412.1 bitscore: 541.6 taxid: 210 
sseqid: WP_024751083.1 bitscore: 539.3 taxid: 210 
sseqid: WP_000753486.1 bitscore: 537.3 taxid: 210 
sseqid: WP_001963517.1 bitscore: 537.3 taxid: 210 
sseqid: WP_079359809.1 bitscore: 537.3 taxid: 210 
sseqid: WP_000753485.1 bitscore: 537.0 taxid: 210 
sseqid: WP_033595811.1 bitscore: 537.0 taxid: 210 
sseqid: WP_058337672.1 bitscore: 537.0 taxid: 210 
sseqid: WP_077656665.1 bitscore: 537.0 taxid: 210 
sseqid: WP_064436257.1 bitscore: 535.8 taxid: 210 
sseqid: WP_001921678.1 bitscore: 535.4 taxid: 210 
sseqid: KNE03025.1 bitscore: 535.4 taxid: 210 
sseqid: WP_024773924.1 bitscore: 535.0 taxid: 210 
sseqid: WP_015087528.1 bitscore: 534.3 taxid: 210 
sseqid: WP_078248142.1 bitscore: 533.9 taxid: 210 
sseqid: WP_000753484.1 bitscore: 533.5 taxid: 210 
sseqid: WP_000753487.1 bitscore: 533.5 taxid: 210 
sseqid: WP_000753488.1 bitscore: 533.1 taxid: 210 
sseqid: WP_001941093.1 bitscore: 53

In [7]:
results.get('NODE_98_length_143507_cov_224.136_11').get_top_hit()

'WP_011577313.1'

### Reading tab-delimited tables

Autometa generates a few different tables in *long* and *wide* formats.

Most of the tables will have a `contig` column to be used as the pandas `DataFrame` index.
Throughout the autometa code base these tables will consistently have `contig` as the index for easy look-up methods.

## K-mers table

In [8]:
# Import pandas library to easily read in tab-delimited tables
import pandas as pd

df = pd.read_csv('dev/kmers.tsv', sep='\t', index_col='contig')

In [9]:
# Note: We can easilty look up the number of rows and columns in our table with the `shape` attribute.
df.shape

(3587, 512)

In [10]:
df.describe()

AAAAA        AAAAT        AAAAC        AAAAG        AAATA  \
count   3587.000000  3587.000000  3587.000000  3587.000000  3587.000000   
mean     129.688040   100.005018    57.866183    70.265403    77.569836   
std      490.711572   380.595919   192.942122   255.260888   339.260178   
min        0.000000     0.000000     0.000000     0.000000     0.000000   
25%        0.000000     0.000000     1.000000     1.000000     0.000000   
50%        5.000000     4.000000     3.000000     4.000000     3.000000   
75%       50.000000    41.000000    27.000000    29.000000    27.000000   
max    10356.000000  8635.000000  3519.000000  5603.000000  8568.000000   

             AAATT        AAATC        AAATG        AAACA        AAACT  ...  \
count  3587.000000  3587.000000  3587.000000  3587.000000  3587.000000  ...   
mean     74.099805    57.123780    52.016727    49.043212    39.641204  ...   
std     272.786141   190.483309   179.009566   164.588022   144.145529  ...   
min       0.000000     0.000000     0.000000     0.000000     0.000000  ...   
25%       0.000000     1.000000     0.000000     1.000000     1.000000  ...   
50%       3.000000     4.000000     3.000000     3.000000     3.000000  ...   
75%      30.000000    27.000000    23.000000    23.000000    20.000000  ...   
max    6672.000000  3292.000000  3265.000000  2900.000000  3564.000000  ...   

             GTGCC        GTGGC        GCACC        GCAGC        GCTCC  \
count  3587.000000  3587.000000  3587.000000  3587.000000  3587.000000   
mean     55.279621    61.176471    79.473097    95.759130    43.639532   
std     226.833744   236.797279   352.880434   370.257865   134.571926   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       1.000000     1.000000     1.000000     2.000000     1.000000   
50%       9.000000    11.000000    13.000000    15.000000    10.000000   
75%      41.000000    46.000000    54.000000    64.500000    38.000000   
max    5891.000000  5660.000000  9894.000000  8731.000000  2752.000000   

             GCCCC         GCCGC         GCGCC        GGACC        GGCCC  
count  3587.000000   3587.000000   3587.000000  3587.000000  3587.000000  
mean     50.939783    153.644829    122.586005    39.891274    60.813493  
std     177.541757    690.738041    560.927086   158.767559   230.312608  
min       0.000000      0.000000      0.000000     0.000000     0.000000  
25%       1.000000      1.000000      1.000000     0.000000     0.000000  
50%      10.000000     16.000000     13.000000     7.000000     7.000000  
75%      42.000000    103.000000     74.000000    30.000000    45.000000  
max    4278.000000  18126.000000  14603.000000  3992.000000  5785.000000  

[8 rows x 512 columns]

Let's look up the contig `NODE_98_length_143507_cov_224.136` from above to see the k-mer frequencies and explore this contig in our other tables...

In [11]:
# Note: Because we have indexed our DataFrame by contigs, 
# we can use the `self.loc` method to find our corresponding data.
df.loc['NODE_98_length_143507_cov_224.136']

AAAAA    2807
AAAAT    1786
AAAAC    1288
AAAAG    1392
AAATA     867
         ... 
GCCCC     287
GCCGC      77
GCGCC      75
GGACC      37
GGCCC      32
Name: NODE_98_length_143507_cov_224.136, Length: 512, dtype: int64

In [12]:
# We can similarly look up a specific value in a row and column
# Syntax: `self.loc[row,col]`
row = 'NODE_98_length_143507_cov_224.136'
col = 'GCCCC'
df.loc[row, col]

287

### Looking up multiple contigs in a DataFrame

We more often are going to want to look up multiple contigs in our table at a time. We can subset our table in one line with `self.isin()`

In [13]:
df.head(n=20)

AAAAA  AAAAT  AAAAC  AAAAG  AAATA  AAATT  \
contig                                                                        
NODE_1_length_1389215_cov_225.275    170    214    544    412    288    254   
NODE_2_length_1166739_cov_224.155   1688   1625   2187   1354    949   1178   
NODE_3_length_1063064_cov_225.095    143    158    419    345    237    229   
NODE_4_length_1031470_cov_223.812    347    225    485    331     90    184   
NODE_5_length_937195_cov_225.122     156    172    382    317    194    198   
NODE_6_length_801699_cov_224.213      97    152    322    265    202    180   
NODE_7_length_734119_cov_224.107      93    109    278    227    168    172   
NODE_8_length_686892_cov_223.785    9083   7161   3519   4526   7106   4912   
NODE_9_length_644926_cov_224.104   10356   8635   3275   5603   8568   6672   
NODE_10_length_622659_cov_224.054     68     81    222    170    137    100   
NODE_11_length_590705_cov_223.126   7164   5753   2787   3655   5286   3818   
NODE_12_length_584723_cov_225.634   6890   5355   2808   3721   5493   3613   
NODE_13_length_533917_cov_222.896   6704   5704   2470   3294   5339   3904   
NODE_14_length_480305_cov_222.789   5679   4544   2326   2767   4245   3017   
NODE_15_length_459631_cov_223.998   1164    707    792    699    482    453   
NODE_16_length_457986_cov_223.76    5710   4338   2242   3061   4330   2838   
NODE_17_length_457780_cov_225.875    713    643    882    610    413    505   
NODE_18_length_457640_cov_224.09      47     70    189    163     88     89   
NODE_19_length_451442_cov_224.264   1057    702    774    687    524    481   
NODE_20_length_436718_cov_222.09    2596   1437   1565   1526    946    946   

                                   AAATC  AAATG  AAACA  AAACT  ...  GTGCC  \
contig                                                         ...          
NODE_1_length_1389215_cov_225.275    892    536    447    511  ...   5891   
NODE_2_length_1166739_cov_224.155   2608   1513   1833   1175  ...   3654   
NODE_3_length_1063064_cov_225.095    724    386    399    394  ...   4530   
NODE_4_length_1031470_cov_223.812    484    325    272    466  ...   3888   
NODE_5_length_937195_cov_225.122     620    378    324    353  ...   3848   
NODE_6_length_801699_cov_224.213     613    324    302    323  ...   3442   
NODE_7_length_734119_cov_224.107     559    316    316    297  ...   3148   
NODE_8_length_686892_cov_223.785    3292   3035   2900   3564  ...    294   
NODE_9_length_644926_cov_224.104    3221   3265   2618   2988  ...    179   
NODE_10_length_622659_cov_224.054    392    205    177    235  ...   2613   
NODE_11_length_590705_cov_223.126   2757   2764   2413   1721  ...    388   
NODE_12_length_584723_cov_225.634   2570   2353   2368   2817  ...    294   
NODE_13_length_533917_cov_222.896   2537   2666   2320   1712  ...    327   
NODE_14_length_480305_cov_222.789   2174   2136   2035   1485  ...    338   
NODE_15_length_459631_cov_223.998    630    531    774    499  ...   1263   
NODE_16_length_457986_cov_223.76    1966   2051   1841   2165  ...    222   
NODE_17_length_457780_cov_225.875   1030    652    739    513  ...   1378   
NODE_18_length_457640_cov_224.09     296    168    166    173  ...   1958   
NODE_19_length_451442_cov_224.264    656    502    806    566  ...   1338   
NODE_20_length_436718_cov_222.09    1227   1040    990    661  ...    725   

                                   GTGGC  GCACC  GCAGC  GCTCC  GCCCC  GCCGC  \
contig                                                                        
NODE_1_length_1389215_cov_225.275   5660   9894   8731   2752   3318  18126   
NODE_2_length_1166739_cov_224.155   4208   4797   6906   2042   4278   9604   
NODE_3_length_1063064_cov_225.095   4292   7448   6461   2011   2519  14146   
NODE_4_length_1031470_cov_223.812   4406   5543   7679   2564   4048  14005   
NODE_5_length_937195_cov_225.122    3678   6377   5703   1834   2201  11991   
NODE_6_length_801699_cov_224.213    3194   5366 

In [14]:
# First let's get the first 20 contigs in the DataFrame to use for our example.
contigs = df.head(20).index

# Now we will check the index of the DataFrame (the contigs) and return a boolean array
df.index.isin(contigs)

# If we want to retrieve the information in the corresponding table,
# we need to provide this array to our DataFrame.
# Notice the `df[filter_criterion]` syntax
df[df.index.isin(contigs)]

AAAAA  AAAAT  AAAAC  AAAAG  AAATA  AAATT  \
contig                                                                        
NODE_1_length_1389215_cov_225.275    170    214    544    412    288    254   
NODE_2_length_1166739_cov_224.155   1688   1625   2187   1354    949   1178   
NODE_3_length_1063064_cov_225.095    143    158    419    345    237    229   
NODE_4_length_1031470_cov_223.812    347    225    485    331     90    184   
NODE_5_length_937195_cov_225.122     156    172    382    317    194    198   
NODE_6_length_801699_cov_224.213      97    152    322    265    202    180   
NODE_7_length_734119_cov_224.107      93    109    278    227    168    172   
NODE_8_length_686892_cov_223.785    9083   7161   3519   4526   7106   4912   
NODE_9_length_644926_cov_224.104   10356   8635   3275   5603   8568   6672   
NODE_10_length_622659_cov_224.054     68     81    222    170    137    100   
NODE_11_length_590705_cov_223.126   7164   5753   2787   3655   5286   3818   
NODE_12_length_584723_cov_225.634   6890   5355   2808   3721   5493   3613   
NODE_13_length_533917_cov_222.896   6704   5704   2470   3294   5339   3904   
NODE_14_length_480305_cov_222.789   5679   4544   2326   2767   4245   3017   
NODE_15_length_459631_cov_223.998   1164    707    792    699    482    453   
NODE_16_length_457986_cov_223.76    5710   4338   2242   3061   4330   2838   
NODE_17_length_457780_cov_225.875    713    643    882    610    413    505   
NODE_18_length_457640_cov_224.09      47     70    189    163     88     89   
NODE_19_length_451442_cov_224.264   1057    702    774    687    524    481   
NODE_20_length_436718_cov_222.09    2596   1437   1565   1526    946    946   

                                   AAATC  AAATG  AAACA  AAACT  ...  GTGCC  \
contig                                                         ...          
NODE_1_length_1389215_cov_225.275    892    536    447    511  ...   5891   
NODE_2_length_1166739_cov_224.155   2608   1513   1833   1175  ...   3654   
NODE_3_length_1063064_cov_225.095    724    386    399    394  ...   4530   
NODE_4_length_1031470_cov_223.812    484    325    272    466  ...   3888   
NODE_5_length_937195_cov_225.122     620    378    324    353  ...   3848   
NODE_6_length_801699_cov_224.213     613    324    302    323  ...   3442   
NODE_7_length_734119_cov_224.107     559    316    316    297  ...   3148   
NODE_8_length_686892_cov_223.785    3292   3035   2900   3564  ...    294   
NODE_9_length_644926_cov_224.104    3221   3265   2618   2988  ...    179   
NODE_10_length_622659_cov_224.054    392    205    177    235  ...   2613   
NODE_11_length_590705_cov_223.126   2757   2764   2413   1721  ...    388   
NODE_12_length_584723_cov_225.634   2570   2353   2368   2817  ...    294   
NODE_13_length_533917_cov_222.896   2537   2666   2320   1712  ...    327   
NODE_14_length_480305_cov_222.789   2174   2136   2035   1485  ...    338   
NODE_15_length_459631_cov_223.998    630    531    774    499  ...   1263   
NODE_16_length_457986_cov_223.76    1966   2051   1841   2165  ...    222   
NODE_17_length_457780_cov_225.875   1030    652    739    513  ...   1378   
NODE_18_length_457640_cov_224.09     296    168    166    173  ...   1958   
NODE_19_length_451442_cov_224.264    656    502    806    566  ...   1338   
NODE_20_length_436718_cov_222.09    1227   1040    990    661  ...    725   

                                   GTGGC  GCACC  GCAGC  GCTCC  GCCCC  GCCGC  \
contig                                                                        
NODE_1_length_1389215_cov_225.275   5660   9894   8731   2752   3318  18126   
NODE_2_length_1166739_cov_224.155   4208   4797   6906   2042   4278   9604   
NODE_3_length_1063064_cov_225.095   4292   7448   6461   2011   2519  14146   
NODE_4_length_1031470_cov_223.812   4406   5543   7679   2564   4048  14005   
NODE_5_length_937195_cov_225.122    3678   6377   5703   1834   2201  11991   
NODE_6_length_801699_cov_224.213    3194   5366 

## Voted Taxids Table (majority_vote.tsv) 

In [15]:
df = pd.read_csv('dev/majority_vote.tsv', sep='\t', index_col='contig')

In [16]:
df.head(3)

taxid superkingdom          phylum  \
contig                                                                   
NODE_98_length_143507_cov_224.136     212     bacteria  proteobacteria   
NODE_99_length_143125_cov_224.739  573569     bacteria  proteobacteria   
NODE_100_length_142487_cov_223.46     212     bacteria  proteobacteria   

                                                   class              order  \
contig                                                                        
NODE_98_length_143507_cov_224.136  epsilonproteobacteria  campylobacterales   
NODE_99_length_143125_cov_224.739    gammaproteobacteria      thiotrichales   
NODE_100_length_142487_cov_223.46  epsilonproteobacteria  campylobacterales   

                                              family         genus  \
contig                                                               
NODE_98_length_143507_cov_224.136  helicobacteraceae  helicobacter   
NODE_99_length_143125_cov_224.739    francisellaceae   francisella   
NODE_100_length_142487_cov_223.46  helicobacteraceae  helicobacter   

                                                    species  
contig                                                       
NODE_98_length_143507_cov_224.136  helicobacter acinonychis  
NODE_99_length_143125_cov_224.739  francisella sp. tx077308  
NODE_100_length_142487_cov_223.46  helicobacter acinonychis

In [17]:
superkingdoms = dict(list(df.groupby('superkingdom')))

In [18]:
# All superkingdom classifications found in DataFrame
superkingdoms.keys()

dict_keys(['bacteria', 'eukaryota', 'unclassified', 'viruses'])

In [19]:
# We can retrieve a subset DataFrame of the superkingdom of interest.
bacteria_df = superkingdoms.get('bacteria')
print(f'master shape: {df.shape} bacteria shape: {bacteria_df.shape}')

master shape: (3250, 8) bacteria shape: (3163, 8)


In [20]:
bacteria_df.head()

taxid superkingdom          phylum  \
contig                                                                    
NODE_98_length_143507_cov_224.136      212     bacteria  proteobacteria   
NODE_99_length_143125_cov_224.739   573569     bacteria  proteobacteria   
NODE_100_length_142487_cov_223.46      212     bacteria  proteobacteria   
NODE_101_length_139096_cov_225.266  146819     bacteria  actinobacteria   
NODE_102_length_138307_cov_223.908  220685     bacteria      firmicutes   

                                                    class              order  \
contig                                                                         
NODE_98_length_143507_cov_224.136   epsilonproteobacteria  campylobacterales   
NODE_99_length_143125_cov_224.739     gammaproteobacteria      thiotrichales   
NODE_100_length_142487_cov_223.46   epsilonproteobacteria  campylobacterales   
NODE_101_length_139096_cov_225.266         actinobacteria   streptomycetales   
NODE_102_length_138307_cov_223.908                bacilli         bacillales   

                                               family         genus  \
contig                                                                
NODE_98_length_143507_cov_224.136   helicobacteraceae  helicobacter   
NODE_99_length_143125_cov_224.739     francisellaceae   francisella   
NODE_100_length_142487_cov_223.46   helicobacteraceae  helicobacter   
NODE_101_length_139096_cov_225.266  streptomycetaceae  streptomyces   
NODE_102_length_138307_cov_223.908        bacillaceae      bacillus   

                                                         species  
contig                                                            
NODE_98_length_143507_cov_224.136       helicobacter acinonychis  
NODE_99_length_143125_cov_224.739       francisella sp. tx077308  
NODE_100_length_142487_cov_223.46       helicobacter acinonychis  
NODE_101_length_139096_cov_225.266  streptomyces europaeiscabiei  
NODE_102_length_138307_cov_223.908          bacillus bataviensis

This table is convenient for inspecting each contigs' taxonomic assignment. However, if we only have a list of taxids we can just as easily reconstruct the full lineage.

In [21]:
#  An Autometa method that will construct each lineage
from autometa.taxonomy.ncbi import NCBI
# First we need to instantiate the NCBI object
ncbi = NCBI('databases/ncbi')

In [22]:
# Code block from above to retrieve ORF specific taxids
taxids = set([attrs.get('taxid') for sseqid,attrs in results.get('NODE_98_length_143507_cov_224.136_11').sseqids.items()])
print(f'taxids: {taxids}')
# Note: There are many other methods available in the NCBI
df = ncbi.get_lineage_dataframe(taxids)

taxids: {210, 212, 992074}


In [23]:
df

superkingdom          phylum                  class              order  \
taxid                                                                           
210        bacteria  proteobacteria  epsilonproteobacteria  campylobacterales   
212        bacteria  proteobacteria  epsilonproteobacteria  campylobacterales   
992074     bacteria  proteobacteria  epsilonproteobacteria  campylobacterales   

                   family         genus                   species  
taxid                                                              
210     helicobacteraceae  helicobacter       helicobacter pylori  
212     helicobacteraceae  helicobacter  helicobacter acinonychis  
992074  helicobacteraceae  helicobacter       helicobacter pylori

We can equally add these taxids back to the DataFrame from which we retrieved them...

## \*.lca.tsv table

In [24]:
lca_filepath = 'dev/scaffolds.orfs.faa.lca.tsv'
lca_df = pd.read_csv(lca_filepath, sep='\t', index_col='qseqid')
lca_df.head()

name     rank  lca
qseqid                                                                     
NODE_98_length_143507_cov_224.136_1  helicobacter acinonychis  species  212
NODE_98_length_143507_cov_224.136_2              helicobacter    genus  209
NODE_98_length_143507_cov_224.136_3              helicobacter    genus  209
NODE_98_length_143507_cov_224.136_4              helicobacter    genus  209
NODE_98_length_143507_cov_224.136_5  helicobacter acinonychis  species  212

In [25]:
df = ncbi.get_lineage_dataframe(lca_df.lca.unique().tolist())
df.head()

superkingdom          phylum           class              order  \
taxid                                                                      
1        unclassified    unclassified    unclassified       unclassified   
2            bacteria    unclassified    unclassified       unclassified   
1703944      bacteria  actinobacteria  actinobacteria   streptomycetales   
2062         bacteria  actinobacteria  actinobacteria   streptomycetales   
2070         bacteria  actinobacteria  actinobacteria  pseudonocardiales   

                     family         genus                   species  
taxid                                                                
1              unclassified  unclassified              unclassified  
2              unclassified  unclassified              unclassified  
1703944   streptomycetaceae  streptomyces  streptomyces sp. cb02400  
2062      streptomycetaceae  unclassified              unclassified  
2070     pseudonocardiaceae  unclassified              unclassified

Notice the returned DataFrame is indexed by taxid. This allows easy merging to the `taxids_df` DataFrame

In [26]:
# Merge DataFrames
merged_df = pd.merge(
        lca_df,
        df,
        how='left',
        left_on='lca',
        right_index=True)

merged_df.head()

name     rank  lca  \
qseqid                                                                        
NODE_98_length_143507_cov_224.136_1  helicobacter acinonychis  species  212   
NODE_98_length_143507_cov_224.136_2              helicobacter    genus  209   
NODE_98_length_143507_cov_224.136_3              helicobacter    genus  209   
NODE_98_length_143507_cov_224.136_4              helicobacter    genus  209   
NODE_98_length_143507_cov_224.136_5  helicobacter acinonychis  species  212   

                                    superkingdom          phylum  \
qseqid                                                             
NODE_98_length_143507_cov_224.136_1     bacteria  proteobacteria   
NODE_98_length_143507_cov_224.136_2     bacteria  proteobacteria   
NODE_98_length_143507_cov_224.136_3     bacteria  proteobacteria   
NODE_98_length_143507_cov_224.136_4     bacteria  proteobacteria   
NODE_98_length_143507_cov_224.136_5     bacteria  proteobacteria   

                                                     class              order  \
qseqid                                                                          
NODE_98_length_143507_cov_224.136_1  epsilonproteobacteria  campylobacterales   
NODE_98_length_143507_cov_224.136_2  epsilonproteobacteria  campylobacterales   
NODE_98_length_143507_cov_224.136_3  epsilonproteobacteria  campylobacterales   
NODE_98_length_143507_cov_224.136_4  epsilonproteobacteria  campylobacterales   
NODE_98_length_143507_cov_224.136_5  epsilonproteobacteria  campylobacterales   

                                                family         genus  \
qseqid                                                                 
NODE_98_length_143507_cov_224.136_1  helicobacteraceae  helicobacter   
NODE_98_length_143507_cov_224.136_2  helicobacteraceae  helicobacter   
NODE_98_length_143507_cov_224.136_3  helicobacteraceae  helicobacter   
NODE_98_length_143507_cov_224.136_4  helicobacteraceae  helicobacter   
NODE_98_length_143507_cov_224.136_5  helicobacteraceae  helicobacter   

                                                      species  
qseqid                                                         
NODE_98_length_143507_cov_224.136_1  helicobacter acinonychis  
NODE_98_length_143507_cov_224.136_2              unclassified  
NODE_98_length_143507_cov_224.136_3              unclassified  
NODE_98_length_143507_cov_224.136_4              unclassified  
NODE_98_length_143507_cov_224.136_5  helicobacter acinonychis

## Markers table format

In [27]:
markers_filepath = 'dev/bacteria.markers.tsv'
markers_df = pd.read_csv(markers_filepath ,sep='\t',index_col='contig')
markers_df.head()

orf  \
contig                                                                      
NODE_13_length_533917_cov_222.896   NODE_13_length_533917_cov_222.896_412   
NODE_126_length_115614_cov_223.525  NODE_126_length_115614_cov_223.525_21   
NODE_126_length_115614_cov_223.525  NODE_126_length_115614_cov_223.525_21   
NODE_126_length_115614_cov_223.525  NODE_126_length_115614_cov_223.525_21   
NODE_127_length_115095_cov_224.529  NODE_127_length_115095_cov_224.529_91   

                                          sacc            sname  score  cutoff  
contig                                                                          
NODE_13_length_533917_cov_222.896   PF00121.13              TIM  315.4  140.20  
NODE_126_length_115614_cov_223.525  PF00712.14    DNA_pol3_beta  139.2   48.70  
NODE_126_length_115614_cov_223.525  PF02767.11  DNA_pol3_beta_2  122.6   49.65  
NODE_126_length_115614_cov_223.525  PF02768.10  DNA_pol3_beta_3   91.8   44.50  
NODE_127_length_115095_cov_224.529   PF08459.6       UvrC_HhH_N  140.3   81.90

In [28]:
from autometa.common.markers import Markers

# load markers is a staticmethod within the Markers class so we can 
# load in the previously annotated markers table
markers_df = Markers.load_markers(markers_filepath, format='wide')
markers_df.head()

sacc                                PF00035.20  PF00113.17  PF00121.13  \
contig                                                                   
NODE_1007_length_15092_cov_223.109         NaN         NaN         NaN   
NODE_1009_length_14996_cov_222.895         NaN         NaN         NaN   
NODE_100_length_142487_cov_223.46          1.0         NaN         NaN   
NODE_1017_length_14855_cov_223.142         NaN         NaN         NaN   
NODE_1023_length_14648_cov_224.155         NaN         NaN         NaN   

sacc                                PF00154.16  PF00162.14  PF00163.14  \
contig                                                                   
NODE_1007_length_15092_cov_223.109         NaN         NaN         NaN   
NODE_1009_length_14996_cov_222.895         NaN         NaN         NaN   
NODE_100_length_142487_cov_223.46          NaN         NaN         NaN   
NODE_1017_length_14855_cov_223.142         NaN         NaN         NaN   
NODE_1023_length_14648_cov_224.155         NaN         NaN         NaN   

sacc                                PF00164.20  PF00177.16  PF00181.18  \
contig                                                                   
NODE_1007_length_15092_cov_223.109         NaN         NaN         NaN   
NODE_1009_length_14996_cov_222.895         1.0         1.0         NaN   
NODE_100_length_142487_cov_223.46          NaN         NaN         NaN   
NODE_1017_length_14855_cov_223.142         NaN         NaN         NaN   
NODE_1023_length_14648_cov_224.155         NaN         NaN         NaN   

sacc                                PF00189.15  ...  PF06574.7  PF06689.8  \
contig                                          ...                         
NODE_1007_length_15092_cov_223.109         NaN  ...        NaN        NaN   
NODE_1009_length_14996_cov_222.895         NaN  ...        NaN        NaN   
NODE_100_length_142487_cov_223.46          NaN  ...        NaN        NaN   
NODE_1017_length_14855_cov_223.142         NaN  ...        NaN        NaN   
NODE_1023_length_14648_cov_224.155         NaN  ...        NaN        NaN   

sacc                                PF07499.8  PF08275.6  PF08459.6  \
contig                                                                
NODE_1007_length_15092_cov_223.109        NaN        NaN        NaN   
NODE_1009_length_14996_cov_222.895        NaN        NaN        NaN   
NODE_100_length_142487_cov_223.46         NaN        NaN        NaN   
NODE_1017_length_14855_cov_223.142        NaN        NaN        NaN   
NODE_1023_length_14648_cov_224.155        NaN        NaN        NaN   

sacc                                PF08529.6  PF10385.4  PF10458.4  \
contig                                                                
NODE_1007_length_15092_cov_223.109        NaN        NaN        NaN   
NODE_1009_length_14996_cov_222.895        NaN        1.0        NaN   
NODE_100_length_142487_cov_223.46         NaN        NaN        NaN   
NODE_1017_length_14855_cov_223.142        NaN        1.0        NaN   
NODE_1023_length_14648_cov_224.155        NaN        NaN        NaN   

sacc                                PF11987.3  PF12344.3  
contig                                                    
NODE_1007_length_15092_cov_223.109        NaN        NaN  
NODE_1009_length_14996_cov_222.895        NaN        NaN  
NODE_100_length_142487_cov_223.46         NaN        NaN  
NODE_1017_length_14855_cov_223.142        NaN        NaN  
NODE_1023_length_14648_cov_224.155        NaN        NaN  

[5 rows x 139 columns]

In [29]:
markers_df = Markers.load_markers(markers_filepath, format='long')
markers_df.head()

sacc  count
contig                                               
NODE_1007_length_15092_cov_223.109  PF02367.12      1
NODE_1009_length_14996_cov_222.895  PF00164.20      1
NODE_1009_length_14996_cov_222.895  PF00177.16      1
NODE_1009_length_14996_cov_222.895  PF00298.14      1
NODE_1009_length_14996_cov_222.895  PF00466.15      1

In [30]:
markers = Markers.load_markers(markers_filepath, format='list')
markers

{'NODE_1007_length_15092_cov_223.109': ['PF02367.12'],
 'NODE_1009_length_14996_cov_222.895': ['PF00584.15',
  'PF03946.9',
  'PF00298.14',
  'PF00687.16',
  'PF00466.15',
  'PF00542.14',
  'PF00562.23',
  'PF04563.10',
  'PF04561.9',
  'PF04560.15',
  'PF04565.11',
  'PF10385.4',
  'PF04997.7',
  'PF04998.12',
  'PF00623.15',
  'PF04983.13',
  'PF05000.12',
  'PF00164.20',
  'PF00177.16'],
 'NODE_100_length_142487_cov_223.46': ['PF05697.8',
  'PF05698.9',
  'PF03948.9',
  'PF01281.14',
  'PF00035.20',
  'PF02938.9',
  'PF03602.10',
  'PF00712.14',
  'PF02768.10',
  'PF00830.14',
  'PF01687.12'],
 'NODE_1017_length_14855_cov_223.142': ['PF04997.7',
  'PF04998.12',
  'PF00623.15',
  'PF04983.13',
  'PF05000.12',
  'PF00562.23',
  'PF04561.9',
  'PF04560.15',
  'PF04565.11',
  'PF10385.4',
  'PF04563.10',
  'PF00542.14',
  'PF00466.15',
  'PF00687.16',
  'PF00298.14',
  'PF03946.9'],
 'NODE_1023_length_14648_cov_224.155': ['PF02882.14', 'PF00763.18'],
 'NODE_1026_length_14554_cov_223.897

In [31]:
markers = Markers.load_markers(markers_filepath, format='counts')
markers

{'NODE_1007_length_15092_cov_223.109': 1,
 'NODE_1009_length_14996_cov_222.895': 19,
 'NODE_100_length_142487_cov_223.46': 11,
 'NODE_1017_length_14855_cov_223.142': 16,
 'NODE_1023_length_14648_cov_224.155': 2,
 'NODE_1026_length_14554_cov_223.897': 1,
 'NODE_102_length_138307_cov_223.908': 6,
 'NODE_1032_length_14379_cov_222.741': 1,
 'NODE_1035_length_14277_cov_224.245': 1,
 'NODE_1037_length_14262_cov_223.873': 1,
 'NODE_1039_length_14197_cov_223.624': 23,
 'NODE_103_length_137756_cov_225.461': 1,
 'NODE_1046_length_13906_cov_224.346': 2,
 'NODE_1052_length_13792_cov_224.116': 1,
 'NODE_1057_length_13739_cov_222.742': 1,
 'NODE_1059_length_13673_cov_223.999': 2,
 'NODE_105_length_136131_cov_224.464': 13,
 'NODE_1073_length_13348_cov_222.786': 1,
 'NODE_1074_length_13345_cov_224.047': 1,
 'NODE_1076_length_13288_cov_223.745': 4,
 'NODE_107_length_135043_cov_223.938': 14,
 'NODE_1080_length_13246_cov_222.788': 1,
 'NODE_1086_length_13138_cov_224.524': 1,
 'NODE_108_length_134368_cov_

# Exposing data to other language formats

With a pandas DataFrame, a variety of methods are available to expose data to a different language format

Examples:

- json objects
- python numpy object
- table with different delimiter
- to python dict object

In [32]:
markers_df = Markers.load_markers(markers_filepath)

In [33]:
markers_df.to_json()

'{"PF00035.20":{"NODE_1007_length_15092_cov_223.109":null,"NODE_1009_length_14996_cov_222.895":null,"NODE_100_length_142487_cov_223.46":1.0,"NODE_1017_length_14855_cov_223.142":null,"NODE_1023_length_14648_cov_224.155":null,"NODE_1026_length_14554_cov_223.897":null,"NODE_102_length_138307_cov_223.908":null,"NODE_1032_length_14379_cov_222.741":null,"NODE_1035_length_14277_cov_224.245":null,"NODE_1037_length_14262_cov_223.873":null,"NODE_1039_length_14197_cov_223.624":null,"NODE_103_length_137756_cov_225.461":null,"NODE_1046_length_13906_cov_224.346":null,"NODE_1052_length_13792_cov_224.116":null,"NODE_1057_length_13739_cov_222.742":null,"NODE_1059_length_13673_cov_223.999":null,"NODE_105_length_136131_cov_224.464":null,"NODE_1073_length_13348_cov_222.786":null,"NODE_1074_length_13345_cov_224.047":null,"NODE_1076_length_13288_cov_223.745":null,"NODE_107_length_135043_cov_223.938":null,"NODE_1080_length_13246_cov_222.788":null,"NODE_1086_length_13138_cov_224.524":null,"NODE_108_length_134

In [34]:
markers_df.to_numpy()

array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [ 1., nan, nan, ..., nan, nan, nan],
       ...,
       [nan,  1., nan, ..., nan, nan, nan],
       [nan,  1., nan, ..., nan, nan, nan],
       [ 1., nan, nan, ..., nan,  1., nan]])

In [35]:
markers_df.to_dict()

{'PF00035.20': {'NODE_1007_length_15092_cov_223.109': nan,
  'NODE_1009_length_14996_cov_222.895': nan,
  'NODE_100_length_142487_cov_223.46': 1.0,
  'NODE_1017_length_14855_cov_223.142': nan,
  'NODE_1023_length_14648_cov_224.155': nan,
  'NODE_1026_length_14554_cov_223.897': nan,
  'NODE_102_length_138307_cov_223.908': nan,
  'NODE_1032_length_14379_cov_222.741': nan,
  'NODE_1035_length_14277_cov_224.245': nan,
  'NODE_1037_length_14262_cov_223.873': nan,
  'NODE_1039_length_14197_cov_223.624': nan,
  'NODE_103_length_137756_cov_225.461': nan,
  'NODE_1046_length_13906_cov_224.346': nan,
  'NODE_1052_length_13792_cov_224.116': nan,
  'NODE_1057_length_13739_cov_222.742': nan,
  'NODE_1059_length_13673_cov_223.999': nan,
  'NODE_105_length_136131_cov_224.464': nan,
  'NODE_1073_length_13348_cov_222.786': nan,
  'NODE_1074_length_13345_cov_224.047': nan,
  'NODE_1076_length_13288_cov_223.745': nan,
  'NODE_107_length_135043_cov_223.938': nan,
  'NODE_1080_length_13246_cov_222.788': na

These methods come with their own arguments to return the designated object and 

```python
# delimiter = ',' or '\t' etc...
markers_df.to_csv('<filepath>', sep='<delimiter>')

```